# Deterministic Real-Business Cycle Model with Diamond-Mortensen-Pissarides search and matching

The economy consists of a number of identical households. The optimal growth problem in discrete time with no uncertainty can be written as follows:
$$
\begin{eqnarray}
 \max_{ \{ c(t), k(t+1), n(t+1), v(t), s(t) \}_{t=0}^{\infty} }
 \sum_{t=0}^{\infty}
 \beta^t
 u(c(t)) - g(n(t))
\end{eqnarray}
$$
subject to
$$
\begin{eqnarray}
 k(t+1) = f(k(t),n(t)) + (1-\delta)k(t) - c(s(t))(1-n(t)) - \gamma v(t) - c(t)
\end{eqnarray}
$$
and
$$
\begin{eqnarray}
 n(t+1) = (1-\rho_x)n(t) + m(n(t),v(t))
\end{eqnarray}
$$

with $k(t) \geq 0$ and given $k(0) > 0$.

In this model ([Merz, 1995](https://www.sciencedirect.com/science/article/abs/pii/0304393295012168)) labor is traded in a process with search externalities for individual households and firms. The rate at which searching workers and firms sign employment contracts will depend on on the tightness of the labor market. This tightness will be determined by the number of traders that are present on the worker side as well as on the firm side. In the current model, this friction is modelled as $m(\cdot)$, which is the matching function.

Rewriting the optimal growth problem as a dynamic programming  problem. Let the choice (or control) variable be next date's capital stock, denoted $k'$. Then the resource constraint, shown in the optimal growth problem, implies that the current consumption is given by $$c=f(k,n)+(1-\delta)k-k'-c_0s^{\eta}(1-n)-\gamma v$$

The optimal growth problem can be written in the following recursive form:
$$
V(k,n) = \max_{ k'\in G(k), n' } 
\{
 u(c) - g(n) + \beta V(k',n')
\}
$$
where $G(k)$ is the constraint correspondence, given by the interval $[0, f(k)+(1-\delta)k]$. This constraint requires that consumption and the capital stock be nonnegative.

TBC ...

In [1]:
# Load packages
using Optim
using Plots
using Statistics
using NLsolve

In [2]:
# Functions
function fun_max(mX)
    # Find maximum of a matrix along the columns
    # Input: mX of dimension m x n
    # Output vMax of dimension n
    iCols = size(mX, 2);
    vMax = zeros(iCols,1);
    for i = 1:iCols
            temp_max = findmax( mX[:,i] );
            vMax[i] = temp_max[1];
    end
    return vMax;
end

function fun_max_index(mX)
    # Find maximum of a matrix along the columns
    # and give the index
    # Input: mX of dimension m x n
    # Output vMax of dimension n
    iCols = size(mX, 2);
    vMax_index = zeros(iCols,1);
    for i = 1:iCols
            temp_max = findmax( mX[:,i] );
            vMax_index[i] = temp_max[2];
    end
    return vMax_index;
end

fun_max_index (generic function with 1 method)

In [3]:
# Structural parameters
pAlpha = 0.36;
pBeta = 0.99;
pDelta = 0.022;
pTheta = 1;
pEta = 1;
pMu_m = 1;
pGamma = 0.05;
pGamma_n = -1/1.25;
pAlpha_m = 0.40;
pRho_x = 0.07;
pMu = 0.004;
pA = 0.05;
pC0 = 0.005;
pRho = 0.95;
pSigmaeps = 0.007;
pMuz = 1;

In [4]:
# Computing the steady state values
PARAMS = [ pAlpha, pAlpha_m, pTheta, pGamma_n, pC0, pEta, pDelta, pRho_x, pMu_m, pGamma, pBeta ];
function f!(F,x,PARAMS)

    # 1  2  3  4  5    6     7
    # c, v, s, k, n, lambda, mu

    pAlpha = PARAMS[1];
    pAlpha_m = PARAMS[2];
    pTheta = PARAMS[3];
    pGamma_n = PARAMS[4];
    pC0 = PARAMS[5];
    pEta = PARAMS[6];
    pDelta = PARAMS[7];
    pRho_x = PARAMS[8];
    pMu_m = PARAMS[9];
    pGamma = PARAMS[10];
    pBeta = PARAMS[11];

    F[1] = x[4]^pAlpha*x[5]^(1-pAlpha) -pDelta*x[4] -pC0*x[3]^pEta*(1-x[5])-pGamma*x[2]-x[1]
    F[2] = (1-pRho_x)*x[5] + pMu_m*x[2]^(1-pAlpha_m)*( x[3]*(1-x[5]) )^pAlpha_m - x[5]
    F[3] = pBeta*( pAlpha*x[4]^(pAlpha-1)*x[5]^(1-pAlpha) + (1-pDelta) ) - 1
    F[4] = pBeta*( -pTheta*x[5]^(-pGamma_n) + x[6]*( (1-pAlpha)*x[4]^pAlpha*x[5]^(-pAlpha)+pC0*x[3]^pEta ) 
                + x[7]*( (1-pRho_x)-pMu_m*pAlpha_m*x[2]^(1-pAlpha_m)*x[3]^pAlpha_m*(1-x[5])^(pAlpha_m-1) ) ) - x[7]
    F[5] = 1/x[1] - x[6]
    F[6] = x[7]*( pMu_m*(1-pAlpha_m)*x[2]^(-pAlpha_m)*( x[3]*(1-x[5]) )^(pAlpha_m) )-pGamma*x[6]
    F[7] = x[7]*pMu_m*x[2]^(1-pAlpha_m)*pAlpha_m*x[3]^(pAlpha_m-1)*(1-x[5])^pAlpha_m-x[6]*pC0*pEta*x[3]^(pEta-1)*(1-x[5])

end


SteadyState = nlsolve((F,x) ->f!(F,x,PARAMS), [ 2.67, 0.02, 2.3, 39, 0.92, 0.37, 0.01 ], iterations = 1000 , method = :newton)

# Defining the steady state
dSss = SteadyState.zero[3];
dKss = SteadyState.zero[4];
dNss = SteadyState.zero[5];

# Display results:
print("Numerical results: ")
print("\n")
print("Steady state capital: ")
print(dKss)
print("\n")
print("Steady state employment: ")
print(dNss)



Numerical results: 
Steady state capital: 39.89232391191
Steady state employment: 0.9132762110134824

In [5]:
# Algorithm related parameters
iIter = 5000;
iGridPointsK = 300;
iGridPointsN = 20;
iToler = 10e-6;

# Constructing the grid
dKmin = dKss * 0.7;
dKmax = dKss * 1.37;
dNmin = dNss * 0.99;
dNmax = dNss * 1.01;


iStepK = (dKmax-dKmin) / (iGridPointsK-1);
vK = collect(dKmin:iStepK:dKmax);
iGridPointsK = size(vK,1);

iStepN = (dNmax-dNmin) / (iGridPointsN-1);
vN = collect(dNmin:iStepN:dNmax);
iGridPointsN = size(vN,1);

In [6]:
mK_S = zeros(iGridPointsK, iGridPointsK);
mN_S = zeros(iGridPointsN, iGridPointsN);

# Storage space
for idxKP = 1:iGridPointsK
    for idxK = 1:iGridPointsK
        mK_S[idxKP,idxK] = vK[idxK];
    end
end

for idxNP = 1:iGridPointsN
    for idxN = 1:iGridPointsN
        mN_S[idxNP,idxN] = vN[idxN];
    end
end


mK = kron( ones(iGridPointsN,iGridPointsN), mK_S  );
mKP = mK';

mN = kron( mN_S, ones(iGridPointsK,iGridPointsK) );
mNP = mN';

TEMP_A = ( 1 ./ pMu_m*dSss );
TEMP_B = ( mNP-(1-pRho_x) .* mN );
TEMP_C = ( ones(size(mN))-mN );
TEMP_D = (-pAlpha_m);
TEMP_E = ( 1 ./ (1-pAlpha_m) );

mV = ( TEMP_A .* TEMP_B .* TEMP_C .^ TEMP_D ) .^ TEMP_E;

TEMP_F = mK.^pAlpha .* mN.^(1-pAlpha);
TEMP_G = -mKP + (1-pDelta).*mK;
TEMP_H = -pC0*dSss^pEta;
TEMP_I = -pGamma.*mV;

mC = TEMP_F + TEMP_G .+ TEMP_H + TEMP_I;

#display( mC )

In [7]:
# Eliminate negative consumption
mCP = mC .> 0;
mPC = ones(iGridPointsK*iGridPointsN, iGridPointsK*iGridPointsN) - mCP;
z = 10e-5;
mC = mC.*mCP + z*mPC;

# Initialize value function
mU = log.( mC ) .+ pTheta.*( ( mN.^(1-pGamma_n) )./(1-pGamma_n) );

mCF = mC;

mVNew = log.(mCF);
global vVOld = fun_max( mU+pBeta*mVNew ); # ( [iGridPointsK*iGridPointsN] x 1 )


vEps = zeros(iIter,1);

In [8]:
global counter = 0;
### Main Iteration - BEGIN ###
for idxIter=1:iIter

 global vVOld;
 global  counter;

 vVNew = fun_max(mU+pBeta*(ones(iGridPointsN*iGridPointsK,1)*vVOld')');

 iDiff = ( abs.(vVOld-vVNew) ) ./ vVOld;

 dEps = sum(sqrt.((iDiff).^2));
 vEps[idxIter,1] = dEps;

 if sum(sqrt.((iDiff).^2)) <= iToler
  vVOld = vVNew;
  break
 else
  vVOld = vVNew;
 end
 
 counter = counter + 1;

end
### Main Iteration - END ###

print("\n");
print("\n");
print("Iterations needed to reach convergence : ")
print(counter);
print("\n");



Iterations needed to reach convergence : 1548


In [9]:
plot(vEps[100:iIter],legend=false,title="Convergence of the value iteration")
xlabel!("iterations")
ylabel!("epsilon")

# Preparing maximum values and indices for policy function
maxR = fun_max(mU+pBeta*(ones(iGridPointsK*iGridPointsN,1)*vVOld')');
idxR = fun_max_index(mU+pBeta*(ones(iGridPointsK*iGridPointsN,1)*vVOld')');

# print("Maximum value");
# print("\n");
# print(maxR);
# print("\n");
# print("\n");
# print("Index")
# print("\n");
# print(idxR);
# print("\n");
# print("\n");
# print("Capital grid");
# print("\n");
# print(vK);
# print("\n");
# print("\n");
# print("Employment grid");
# print("\n");
# print(vN);

In [10]:
print("\n");
print("\n");

# Extending the grid where we evaluate variables
vK_L = kron( ones(iGridPointsN,1), vK );
vN_L = reshape( kron(vN, ones(iGridPointsK)), iGridPointsK*iGridPointsN,1) ;


policyC = ones(iGridPointsK*iGridPointsN,1);

for idx = 1:iGridPointsK*iGridPointsN
    policyC[idx] = mC[ floor(Int, idxR[idx]) , idx ]
end

policyC

graph1=plot(vN_L,vK_L,policyC, st = [:surface, :contourf],legend=false,title="Consumption decision")
xlabel!("N")
ylabel!("K")
savefig(graph1,"../output/graph1")

graph2=plot(vN_L,vK_L,policyC, st = [:surface], camera=(49,29),title="Consumption decision")
xlabel!("N")
ylabel!("K")
savefig(graph2,"../output/graph2")

# Extending the grid where we evaluate variables
vK_L = kron( ones(iGridPointsN,1), vK );
vN_L = kron(vN, ones(iGridPointsK));

# Constructing policy functions: Storage space
vKP = zeros(iGridPointsN*iGridPointsK,1);
vC_L = zeros(iGridPointsN*iGridPointsK,1);
vNP = zeros(iGridPointsN*iGridPointsK,1);

VA = zeros(iGridPointsN*iGridPointsK,1);
VB = zeros(iGridPointsN*iGridPointsK,1);
vV = zeros(iGridPointsN*iGridPointsK,1);

#display(mC)




Arrays have incorrect length or dimension.


In [14]:
# Plot consumption decision
plot(vN_L,vK_L,policyC, st = [:surface], camera=(49,29),title="Consumption decision")
scatter!([dNss],[dKss],legend=false)
xlabel!("N")
ylabel!("K")